In [43]:
import pandas as pd
import os
from datetime import datetime, timedelta
import glob
import pandas as pd
import random
import numpy as np
import seaborn as sns
import ast
import json
import os
import re
import itertools
import folium
import hdbscan
import h3

from scipy.spatial.transform import Rotation as R
from scipy.spatial.distance import euclidean
from scipy.spatial.distance import pdist, squareform
from sklearn.cluster import DBSCAN
from sklearn.neighbors import NearestNeighbors
import matplotlib.pyplot as plt
import matplotlib.pylab as pl
import matplotlib.patches as patches
from pydp.algorithms.numerical_mechanisms import LaplaceMechanism
from itertools import combinations
from collections import defaultdict
from collections import Counter
from typing import Dict, Set, List, Optional, Tuple

In [44]:
df_gps = pd.read_csv("C:\\Users\\dmc\\Desktop\\extracted_trips_data.csv")

df_people = pd.read_csv("C:\\Users\\dmc\\Desktop\\individuals_dataset.csv")
df_people = df_people[df_people['GPS_RECORD'] == True]

df_merged = pd.merge(
    df_gps,
    df_people[['ID', 'SEX', 'AGE', 'PRO_CAT', 'WEIGHT_INDIV']],
    left_on='person_id',
    right_on='ID',
    how='inner'
).drop(columns='ID')

h3_resolution = 10

df_merged['start_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['start_lat'], row['start_lon'], h3_resolution), axis=1)
df_merged['end_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['end_lat'], row['end_lon'], h3_resolution), axis=1)

media_peso = df_merged['WEIGHT_INDIV'].mean()

In [45]:
# mode = "SEX"
# mode = "AGE"
mode = "PRO_CAT"

In [46]:
if mode == "SEX":
    df_man = df_merged[df_merged["SEX"] == "Man"]
    df_woman = df_merged[df_merged["SEX"] == "Woman"]
    print("Split fatto per SEX")
    
elif mode == "AGE":
    df_10_19 = df_merged[(df_merged["AGE"] >= 10) & (df_merged["AGE"] <= 19)]
    df_20_29 = df_merged[(df_merged["AGE"] >= 20) & (df_merged["AGE"] <= 29)]
    df_30_39 = df_merged[(df_merged["AGE"] >= 30) & (df_merged["AGE"] <= 39)]
    df_40_49 = df_merged[(df_merged["AGE"] >= 40) & (df_merged["AGE"] <= 49)]
    df_50_59 = df_merged[(df_merged["AGE"] >= 50) & (df_merged["AGE"] <= 59)]
    df_60_69 = df_merged[(df_merged["AGE"] >= 60) & (df_merged["AGE"] <= 69)]
    df_over70 = df_merged[(df_merged["AGE"] >= 70)]
    print("Split fatto per AGE")
    
elif mode == "PRO_CAT":
    df_procat_1 = df_merged[df_merged["PRO_CAT"] == 1]
    df_procat_2 = df_merged[df_merged["PRO_CAT"] == 2]
    df_procat_3 = df_merged[df_merged["PRO_CAT"] == 3]
    df_procat_4 = df_merged[df_merged["PRO_CAT"] == 4]
    df_procat_5 = df_merged[df_merged["PRO_CAT"] == 5]
    df_procat_6 = df_merged[df_merged["PRO_CAT"] == 6]
    df_procat_7 = df_merged[df_merged["PRO_CAT"] == 7]
    df_procat_8 = df_merged[df_merged["PRO_CAT"] == 8]
    print("Split fatto per PRO_CAT")
    
else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

Split fatto per PRO_CAT


In [47]:
if mode == "SEX":
    od_matrix_first_man = df_man.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_man.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_woman = df_woman.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_woman.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "AGE":
    od_matrix_first_10_19 = df_10_19.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_10_19.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_20_29 = df_20_29.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_20_29.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_30_39 = df_30_39.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_30_39.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_40_49 = df_40_49.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_40_49.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_50_59 = df_50_59.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_50_59.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_60_69 = df_60_69.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_60_69.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_over70 = df_over70.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_over70.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "PRO_CAT":
    od_matrix_first_procat_1 = df_procat_1.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_1.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_2 = df_procat_2.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_2.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_3 = df_procat_3.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_3.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_4 = df_procat_4.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_4.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_5 = df_procat_5.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_5.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_6 = df_procat_6.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_6.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_7 = df_procat_7.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_7.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_8 = df_procat_8.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_8.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [48]:
parent_hexes = ["861fb4667ffffff", "861fb4677ffffff", "861fb466fffffff", "861fb4647ffffff", "861fb475fffffff"]

target_resolution = 10
start_valid_h3 = set()
end_valid_h3 = set()

for parent in parent_hexes:
    children = h3.cell_to_children(parent, target_resolution)
    for child in children:
        start_valid_h3.add(child)
        end_valid_h3.add(child)

if mode == "SEX":
    mask_man = ((od_matrix_first_man["start_h3"].isin(start_valid_h3)) & (od_matrix_first_man["end_h3"].isin(end_valid_h3)))
    mask_woman = ((od_matrix_first_woman["start_h3"].isin(start_valid_h3)) & (od_matrix_first_woman["end_h3"].isin(end_valid_h3)))

    od_matrix_first_man = od_matrix_first_man[mask_man].copy()
    od_matrix_first_woman = od_matrix_first_woman[mask_woman].copy()

elif mode == "AGE":
    mask_10_19 = ((od_matrix_first_10_19["start_h3"].isin(start_valid_h3)) & (od_matrix_first_10_19["end_h3"].isin(end_valid_h3)))
    mask_20_29 = ((od_matrix_first_20_29["start_h3"].isin(start_valid_h3)) & (od_matrix_first_20_29["end_h3"].isin(end_valid_h3)))
    mask_30_39 = ((od_matrix_first_30_39["start_h3"].isin(start_valid_h3)) & (od_matrix_first_30_39["end_h3"].isin(end_valid_h3)))
    mask_40_49 = ((od_matrix_first_40_49["start_h3"].isin(start_valid_h3)) & (od_matrix_first_40_49["end_h3"].isin(end_valid_h3)))
    mask_50_59 = ((od_matrix_first_50_59["start_h3"].isin(start_valid_h3)) & (od_matrix_first_50_59["end_h3"].isin(end_valid_h3)))
    mask_60_69 = ((od_matrix_first_60_69["start_h3"].isin(start_valid_h3)) & (od_matrix_first_60_69["end_h3"].isin(end_valid_h3)))
    mask_over70 = ((od_matrix_first_over70["start_h3"].isin(start_valid_h3)) & (od_matrix_first_over70["end_h3"].isin(end_valid_h3)))

    od_matrix_first_10_19 = od_matrix_first_10_19[mask_10_19].copy()
    od_matrix_first_20_29 = od_matrix_first_20_29[mask_20_29].copy()
    od_matrix_first_30_39 = od_matrix_first_30_39[mask_30_39].copy()
    od_matrix_first_40_49 = od_matrix_first_40_49[mask_40_49].copy()
    od_matrix_first_50_59 = od_matrix_first_50_59[mask_50_59].copy()
    od_matrix_first_60_69 = od_matrix_first_60_69[mask_60_69].copy()
    od_matrix_first_over70 = od_matrix_first_over70[mask_over70].copy()

elif mode == "PRO_CAT":
    mask_procat_1 = ((od_matrix_first_procat_1["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_1["end_h3"].isin(end_valid_h3)))
    mask_procat_2 = ((od_matrix_first_procat_2["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_2["end_h3"].isin(end_valid_h3)))
    mask_procat_3 = ((od_matrix_first_procat_3["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_3["end_h3"].isin(end_valid_h3)))
    mask_procat_4 = ((od_matrix_first_procat_4["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_4["end_h3"].isin(end_valid_h3)))
    mask_procat_5 = ((od_matrix_first_procat_5["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_5["end_h3"].isin(end_valid_h3)))
    mask_procat_6 = ((od_matrix_first_procat_6["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_6["end_h3"].isin(end_valid_h3)))
    mask_procat_7 = ((od_matrix_first_procat_7["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_7["end_h3"].isin(end_valid_h3)))
    mask_procat_8 = ((od_matrix_first_procat_8["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_8["end_h3"].isin(end_valid_h3)))

    od_matrix_first_procat_1 = od_matrix_first_procat_1[mask_procat_1].copy()
    od_matrix_first_procat_2 = od_matrix_first_procat_2[mask_procat_2].copy()
    od_matrix_first_procat_3 = od_matrix_first_procat_3[mask_procat_3].copy()
    od_matrix_first_procat_4 = od_matrix_first_procat_4[mask_procat_4].copy()
    od_matrix_first_procat_5 = od_matrix_first_procat_5[mask_procat_5].copy()
    od_matrix_first_procat_6 = od_matrix_first_procat_6[mask_procat_6].copy()
    od_matrix_first_procat_7 = od_matrix_first_procat_7[mask_procat_7].copy()
    od_matrix_first_procat_8 = od_matrix_first_procat_8[mask_procat_8].copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [49]:
if mode == "SEX":
    od_matrix_man = od_matrix_first_man.copy()
    od_matrix_woman = od_matrix_first_woman.copy()

elif mode == "AGE":
    od_matrix_10_19 = od_matrix_first_10_19.copy()
    od_matrix_20_29 = od_matrix_first_20_29.copy()
    od_matrix_30_39 = od_matrix_first_30_39.copy()
    od_matrix_40_49 = od_matrix_first_40_49.copy()
    od_matrix_50_59 = od_matrix_first_50_59.copy()
    od_matrix_60_69 = od_matrix_first_60_69.copy()
    od_matrix_over70 = od_matrix_first_over70.copy()

elif mode == "PRO_CAT":
    od_matrix_procat_1 = od_matrix_first_procat_1.copy()
    od_matrix_procat_2 = od_matrix_first_procat_2.copy()
    od_matrix_procat_3 = od_matrix_first_procat_3.copy()
    od_matrix_procat_4 = od_matrix_first_procat_4.copy()
    od_matrix_procat_5 = od_matrix_first_procat_5.copy()
    od_matrix_procat_6 = od_matrix_first_procat_6.copy()
    od_matrix_procat_7 = od_matrix_first_procat_7.copy()
    od_matrix_procat_8 = od_matrix_first_procat_8.copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [50]:
if mode == "SEX":
    filtered_df_man = df_merged.merge(od_matrix_man[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_woman = df_merged.merge(od_matrix_woman[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "AGE":
    filtered_df_10_19 = df_merged.merge(od_matrix_10_19[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_20_29 = df_merged.merge(od_matrix_20_29[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_30_39 = df_merged.merge(od_matrix_30_39[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_40_49 = df_merged.merge(od_matrix_40_49[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_50_59 = df_merged.merge(od_matrix_50_59[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_60_69 = df_merged.merge(od_matrix_60_69[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_over70 = df_merged.merge(od_matrix_over70[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "PRO_CAT":
    filtered_df_procat_1 = df_merged.merge(od_matrix_procat_1[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_2 = df_merged.merge(od_matrix_procat_2[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_3 = df_merged.merge(od_matrix_procat_3[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_4 = df_merged.merge(od_matrix_procat_4[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_5 = df_merged.merge(od_matrix_procat_5[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_6 = df_merged.merge(od_matrix_procat_6[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_7 = df_merged.merge(od_matrix_procat_7[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_8 = df_merged.merge(od_matrix_procat_8[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [51]:
class H3TreeNode:
    """Nodo dell'albero gerarchico H3"""
    def __init__(self, h3_id: str, resolution: int, total_weight: int = 0, count: int = 0):
        self.h3_id = h3_id
        self.resolution = resolution
        self.total_weight = total_weight
        self.count = count
        self.children: Dict[str, 'H3TreeNode'] = {}
        self.parent: Optional['H3TreeNode'] = None
    
    def add_child(self, child: 'H3TreeNode'):
        """Aggiunge un figlio al nodo"""
        self.children[child.h3_id] = child
        child.parent = self
    
    def add_weight(self, weight: int):
        self.total_weight += weight
        if self.parent:
            self.parent.add_weight(weight)
    
    def add_count(self, count: int):
        self.count += count
        if self.parent:
            self.parent.add_count(count)
    
    def __repr__(self):
        return (f"H3Node(id={self.h3_id}, res={self.resolution}, "
                f"total_weight={self.total_weight}, count={self.count}, children={len(self.children)})")

class H3HierarchicalTree:
    def __init__(self, od_matrix: pd.DataFrame, target_resolution: int = 11, hex_column: str = 'start_h3'):
        self.od_matrix = od_matrix
        self.target_resolution = target_resolution
        self.hex_column = hex_column  # 'start_h3' o 'end_h3'
        self.nodes: Dict[str, H3TreeNode] = {}
        self.root = None
        self.min_resolution = None  # Sarà calcolato dinamicamente
        
    def get_all_hexagons(self) -> Set[str]:
        """Estrae tutti gli esagoni unici dalla colonna specificata"""
        return set(self.od_matrix[self.hex_column].unique())
    
    def get_resolution_coverage(self, hexagons: Set[str], target_res: int) -> Set[str]:
        """
        Ottiene tutti gli esagoni di risoluzione target che coprono l'area
        definita dagli esagoni di input
        """
        coverage_hexagons = set()
        
        for hex_id in hexagons:
            current_res = h3.get_resolution(hex_id)
            
            if current_res == target_res:
                coverage_hexagons.add(hex_id)
            elif current_res < target_res:
                # Dobbiamo espandere a risoluzione più alta
                children = self._get_all_children_at_resolution(hex_id, target_res)
                coverage_hexagons.update(children)
            else:
                # Dobbiamo salire a risoluzione più bassa
                parent = h3.cell_to_parent(hex_id, target_res)
                coverage_hexagons.add(parent)
        
        return coverage_hexagons
    
    def find_optimal_min_resolution(self, hexagons: Set[str]) -> int:
        """
        Trova la risoluzione più alta dove c'è ancora un solo nodo che copre tutti gli esagoni
        """
        print("🔍 Analizzando risoluzione ottimale per radice...")
        
        # Per ogni risoluzione da 0 alla target, conta quanti nodi servono per coprire tutti gli esagoni
        resolution_stats = {}
        
        for resolution in range(0, self.target_resolution + 1):
            ancestors = set()
            for hex_id in hexagons:
                current_res = h3.get_resolution(hex_id)
                if current_res >= resolution:
                    ancestor = h3.cell_to_parent(hex_id, resolution)
                    ancestors.add(ancestor)
                else:
                    # L'esagono è già a risoluzione più bassa, aggiungi direttamente
                    ancestors.add(hex_id)
            
            resolution_stats[resolution] = len(ancestors)
            print(f"  - Risoluzione {resolution}: {len(ancestors)} nodi")
        
        # Trova la risoluzione più alta con count = 1
        optimal_resolution = 0
        for resolution in range(self.target_resolution, -1, -1):
            if resolution_stats[resolution] == 1:
                optimal_resolution = resolution
                break
        
        print(f"✅ Risoluzione ottimale trovata: {optimal_resolution}")
        return optimal_resolution
    
    def get_siblings(self, node_id: str) -> List[str]:
        """Restituisce gli h3_id dei nodi fratelli di node_id (stesso genitore, escluso node_id stesso)"""
        if node_id not in self.nodes:
            return []

        node = self.nodes[node_id]
        parent = node.parent
        if parent is None:
            # Nodo root, non ha fratelli
            return []

        siblings = [child.h3_id for child in parent.children.values() if child.h3_id != node_id]
        return siblings
    
    def get_parent(self, node_id: str) -> Optional[str]:
        """Restituisce l'h3_id del genitore del nodo dato, o None se root o nodo non trovato"""
        if node_id not in self.nodes:
            return None
        node = self.nodes[node_id]
        if node.parent is None:
            return None
        return node.parent.h3_id
    
    def _get_all_children_at_resolution(self, hex_id: str, target_res: int) -> Set[str]:
        """Ricorsivamente ottiene tutti i figli a una risoluzione specifica"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == target_res:
            return {hex_id}
        elif current_res > target_res:
            # Non dovrebbe succedere in questo contesto
            return set()
        
        children = set()
        direct_children = h3.cell_to_children(hex_id, current_res + 1)
        
        for child in direct_children:
            children.update(self._get_all_children_at_resolution(child, target_res))
        
        return children
    
    def build_hierarchy_path(self, hex_id: str, min_resolution: int) -> List[str]:
        """Costruisce il percorso gerarchico da un esagono fino alla risoluzione minima"""
        path = [hex_id]
        current = hex_id
        current_res = h3.get_resolution(current)
        
        while current_res > min_resolution:
            parent = h3.cell_to_parent(current, current_res - 1)
            path.append(parent)
            current = parent
            current_res -= 1
        
        return path
    
    def create_tree_structure(self):
        """Crea la struttura dell'albero ottimizzato"""
        target_hexagons = self.get_all_hexagons()
        
        # Ottieni copertura completa alla risoluzione target
        coverage_hexagons = self.get_resolution_coverage(target_hexagons, self.target_resolution)
        
        # Trova la risoluzione minima ottimale (quella più alta con count=1)
        self.min_resolution = self.find_optimal_min_resolution(coverage_hexagons)
        
        print(f"🏗️ Costruendo albero da risoluzione {self.min_resolution} a {self.target_resolution}")
        
        # Costruisci tutti i percorsi gerarchici
        all_paths = []
        for hex_id in coverage_hexagons:
            path = self.build_hierarchy_path(hex_id, self.min_resolution)
            all_paths.append(path)
        
        # Crea tutti i nodi
        for path in all_paths:
            for hex_id in path:
                if hex_id not in self.nodes:
                    resolution = h3.get_resolution(hex_id)
                    self.nodes[hex_id] = H3TreeNode(hex_id, resolution)
        
        # Stabilisci relazioni parent-child
        for path in all_paths:
            for i in range(len(path) - 1):
                child_id = path[i]
                parent_id = path[i + 1]
                self.nodes[parent_id].add_child(self.nodes[child_id])
        
        # Identifica la radice
        self.root = self.nodes[self._find_root_hexagon(coverage_hexagons, self.min_resolution)]
        
        return self
    
    def _find_root_hexagon(self, hexagons: Set[str], min_resolution: int) -> str:
        """Trova l'esagono radice che contiene tutti gli altri"""
        sample_hex = next(iter(hexagons))
        return h3.cell_to_parent(sample_hex, min_resolution)
    
    def populate_counts(self):
        # Raggruppa per esagono le due metriche
        agg_df = self.od_matrix.groupby(self.hex_column).agg({'total_weight': 'sum', 'count': 'sum'}).reset_index()
        
        for _, row in agg_df.iterrows():
            hex_id = row[self.hex_column]
            weight = int(row['total_weight'])
            count = int(row['count'])
            
            target_hex = self._map_to_target_resolution(hex_id)
            
            if target_hex in self.nodes:
                self.nodes[target_hex].add_weight(weight)
                self.nodes[target_hex].add_count(count)
            else:
                print(f"⚠️ Avviso: esagono {target_hex} non trovato nell'albero")
        
        return self
    
    def _map_to_target_resolution(self, hex_id: str) -> str:
        """Mappa un esagono alla risoluzione target"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == self.target_resolution:
            return hex_id
        elif current_res < self.target_resolution:
            # Prendi il primo figlio disponibile (potrebbe essere migliorato)
            children = self._get_all_children_at_resolution(hex_id, self.target_resolution)
            return next(iter(children)) if children else hex_id
        else:
            return h3.cell_to_parent(hex_id, self.target_resolution)
    
    def get_tree_statistics(self) -> Dict:
        """Ottiene statistiche dell'albero"""
        if not self.root:
            return {}
        
        stats = {
            'total_nodes': len(self.nodes),
            'root_resolution': self.root.resolution,
            'min_resolution': self.min_resolution,
            'target_resolution': self.target_resolution,
            'total_weight': self.root.total_weight,
            'nodes_by_resolution': defaultdict(int),
            'resolution_range': f"{self.min_resolution} → {self.target_resolution}"
        }
        
        for node in self.nodes.values():
            stats['nodes_by_resolution'][node.resolution] += 1
        
        return stats
    
    def print_tree(self, max_children_per_level: int = 10):
        if not self.root:
            print("❌ Albero non costruito")
            return
        
        print(f"\n🌳 STRUTTURA ALBERO OTTIMIZZATA")
        print(f"📏 Range risoluzione: {self.min_resolution} → {self.target_resolution}")
        print("=" * 80)
        
        def _print_node(node: H3TreeNode, depth: int = 0, is_last: bool = True, prefix: str = ""):
            connector = "└─ " if is_last else "├─ "
            print(f"{prefix}{connector}{node.h3_id} (res:{node.resolution}, total_weight:{node.total_weight}, count:{node.count}, children:{len(node.children)})")
            
            if is_last:
                child_prefix = prefix + "   "
            else:
                child_prefix = prefix + "│  "
            
            children_list = list(node.children.values())
            
            if len(children_list) <= max_children_per_level:
                for i, child in enumerate(children_list):
                    is_last_child = (i == len(children_list) - 1)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
            else:
                for i in range(max_children_per_level):
                    child = children_list[i]
                    is_last_child = (i == max_children_per_level - 1) and (len(children_list) == max_children_per_level)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
                
                remaining = len(children_list) - max_children_per_level
                print(f"{child_prefix}└─ ... e altri {remaining} figli con stesso pattern")
        
        _print_node(self.root, 0, True, "")

def create_h3_hierarchical_tree(od_matrix_df: pd.DataFrame, target_resolution: int = 10, hex_column: str = 'start_h3'):
    """
    Crea un albero gerarchico H3 ottimizzato dal dataset OD matrix
    
    Args:
        od_matrix_df: DataFrame con colonne 'start_h3', 'end_h3', 'count'
        target_resolution: Risoluzione target per le foglie dell'albero
        hex_column: Colonna da analizzare ('start_h3' o 'end_h3')
    
    Returns:
        H3HierarchicalTree: Albero gerarchico costruito e ottimizzato
    """
    
    tree = H3HierarchicalTree(od_matrix_df, target_resolution, hex_column)
    tree.create_tree_structure()
    tree.populate_counts()
    
    stats = tree.get_tree_statistics()
    print(f"\n📈 STATISTICHE ALBERO OTTIMIZZATO ({hex_column.upper()})")
    print("=" * 50)
    print(f"• Nodi totali: {stats['total_nodes']:,}")
    print(f"• Range risoluzione: {stats['resolution_range']}")
    print(f"• Risoluzione radice: {stats['root_resolution']}")
    print(f"• Risoluzione foglie: {stats['target_resolution']}")
    print(f"• Nodi per risoluzione:")
    for res in sorted(stats['nodes_by_resolution'].keys()):
        print(f"  - Risoluzione {res}: {stats['nodes_by_resolution'][res]:,} nodi")
    
    # Calcola risparmio in nodi
    total_resolutions_possible = target_resolution + 1  # da 0 a target
    resolutions_used = len(stats['nodes_by_resolution'])
    resolutions_saved = total_resolutions_possible - resolutions_used
    
    print(f"\n💡 OTTIMIZZAZIONI:")
    print(f"• Risoluzioni risparmiate: {resolutions_saved}")
    print(f"• Efficienza albero: {resolutions_used}/{total_resolutions_possible} livelli utilizzati")
    
    tree.print_tree()
    
    return tree

In [52]:
if mode == "SEX":
    tree_start_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='start_h3')
    tree_start_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='start_h3')

    tree_end_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='end_h3')
    tree_end_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='end_h3')

elif mode == "AGE":
    tree_start_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='start_h3')
    tree_start_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='start_h3')
    tree_start_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='start_h3')
    tree_start_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='start_h3')
    tree_start_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='start_h3')
    tree_start_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='start_h3')
    tree_start_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='start_h3')

    tree_end_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='end_h3')
    tree_end_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='end_h3')
    tree_end_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='end_h3')
    tree_end_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='end_h3')
    tree_end_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='end_h3')
    tree_end_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='end_h3')
    tree_end_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='end_h3')

elif mode == "PRO_CAT":
    tree_start_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='start_h3')
    tree_start_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='start_h3')
    tree_start_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='start_h3')
    tree_start_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='start_h3')
    tree_start_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='start_h3')
    tree_start_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='start_h3')
    tree_start_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='start_h3')
    tree_start_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='start_h3')

    tree_end_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='end_h3')
    tree_end_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='end_h3')
    tree_end_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='end_h3')
    tree_end_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='end_h3')
    tree_end_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='end_h3')
    tree_end_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='end_h3')
    tree_end_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='end_h3')
    tree_end_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='end_h3')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

🔍 Analizzando risoluzione ottimale per radice...
  - Risoluzione 0: 1 nodi
  - Risoluzione 1: 1 nodi
  - Risoluzione 2: 1 nodi
  - Risoluzione 3: 1 nodi
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 34 nodi
  - Risoluzione 8: 151 nodi
  - Risoluzione 9: 423 nodi
  - Risoluzione 10: 694 nodi
✅ Risoluzione ottimale trovata: 4
🏗️ Costruendo albero da risoluzione 4 a 10

📈 STATISTICHE ALBERO OTTIMIZZATO (START_H3)
• Nodi totali: 1,310
• Range risoluzione: 4 → 10
• Risoluzione radice: 4
• Risoluzione foglie: 10
• Nodi per risoluzione:
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 34 nodi
  - Risoluzione 8: 151 nodi
  - Risoluzione 9: 423 nodi
  - Risoluzione 10: 694 nodi

💡 OTTIMIZZAZIONI:
• Risoluzioni risparmiate: 4
• Efficienza albero: 7/11 livelli utilizzati

🌳 STRUTTURA ALBERO OTTIMIZZATA
📏 Range risoluzione: 4 → 10
└─ 841fb47ffffffff (res:4, total_weight:2371901, count:1085, children:

In [53]:
import numpy as np
import pandas as pd

# Il senso del lattice è di esplorare tutte le combinazioni di livelli di risoluzioni (lvlo e lvld)
# L'algoritmo scorre questo reticolo e cerca la generalizzazione più fine possibile (cioè con lvlo+lvld minimo) 
# che rispetti il vincolo: la somma dei total_weight delle classi non k-anonime (quelle con total_weight < k) sia ≤ S (budget di soppressione).

# Se una coppia (lvlo, lvld) è "accettabile", tutte le sue generalizzazioni (livelli più alti, quindi risoluzioni più basse) sono automaticamente accettabili. 
# Se è "non accettabile", tutte le sue specializzazioni (risoluzioni più alte) sono automaticamente non accettabili.

class Lattice2DWeight:
    """
    OIGH adattata per H3HierarchicalTree
    k-anonimita' basata su total_weight, count viene aggregato insieme
    """
    def __init__(self, od_matrix, tree_start, tree_end, k, S):
        self.od_matrix = od_matrix.copy()
        self.tree_start = tree_start
        self.tree_end = tree_end
        self.k = k
        self.S = S
        self.total_vol = self.od_matrix['total_weight'].sum()

        self.L_start = max(node.resolution for node in tree_start.nodes.values())
        self.L_end   = max(node.resolution for node in tree_end.nodes.values())

        self.nodes = {}
        self.add_node(self.L_start, self.L_end, parents=[])
        self.max_level_found = np.inf
        self.od_matrix_agg = None
        self.best_avg_class_size = np.inf

    def add_node(self, lvlo, lvld, parents):
        if (lvlo, lvld) not in self.nodes:
            node = LatticeNodeWeight(lvlo, lvld, parents=parents, lattice=self)
            self.nodes[(lvlo, lvld)] = node
            if lvlo > self.tree_start.min_resolution:
                self.add_node(lvlo-1, lvld, [node])
                node.children.append(self.nodes[(lvlo-1, lvld)])
            if lvld > self.tree_end.min_resolution:
                self.add_node(lvlo, lvld-1, [node])
                node.children.append(self.nodes[(lvlo, lvld-1)])
        else:
            self.nodes[(lvlo, lvld)].parents += parents


class LatticeNodeWeight:
    def __init__(self, lvlo, lvld, parents, lattice):
        self.lattice = lattice
        self.lvlo = lvlo
        self.lvld = lvld
        self.parents = parents
        self.children = []
        self.anonymous = None
        self.visited = False

    def evaluate(self):
        self.visited = True
        if self.lvlo + self.lvld <= self.lattice.max_level_found:

            if self.children and not self.children[0].visited:
                self.children[0].evaluate()

            if self.anonymous is None:
                od_matrix_agg = self.get_aggregation()

                self.avg_class_size = self.get_mean_agg_level(od_matrix_agg)
                self.suppr_vol = od_matrix_agg[od_matrix_agg['total_weight'] < self.lattice.k]['total_weight'].sum()

                if self.suppr_vol > self.lattice.S:
                    self.tag_unanonymous()
                else:
                    if self.lvlo + self.lvld == self.lattice.max_level_found:
                        if (self.lattice.od_matrix_agg is None) or (self.avg_class_size < self.lattice.best_avg_class_size):
                            self.lattice.od_matrix_agg = od_matrix_agg
                            self.lattice.best_avg_class_size = self.avg_class_size
                    else:
                        self.lattice.max_level_found = self.lvlo + self.lvld
                        self.lattice.od_matrix_agg = od_matrix_agg
                        self.lattice.best_avg_class_size = self.avg_class_size
                    self.tag_anonymous()

            if len(self.children) > 1 and not self.children[1].visited:
                self.children[1].evaluate()

    def tag_anonymous(self):
        if self.anonymous is None:
            self.anonymous = True
            for c in self.children:
                c.tag_anonymous()

    def tag_unanonymous(self):
        if self.anonymous is None:
            self.anonymous = False
            for p in self.parents:
                p.tag_unanonymous()

    def map_to_level(self, h, target_res, tree):
        node = tree.nodes.get(h)
        if node is None:
            return h
        while node and node.resolution > target_res:
            node = node.parent
        return node.h3_id if node else h

    def get_aggregation(self):
        df = self.lattice.od_matrix.copy()

        # aggrega start e end
        df['start_gen'] = df['start_h3'].apply(lambda h: self.map_to_level(h, self.lvlo, self.lattice.tree_start))
        df['end_gen']   = df['end_h3'].apply(lambda h: self.map_to_level(h, self.lvld, self.lattice.tree_end))

        # aggrega total_weight e count
        agg = df.groupby(['start_gen', 'end_gen']).agg({
            'total_weight': 'sum',   # k-anonimity basata su total_weight
            'count': 'sum'           # aggregazione count
        }).reset_index()

        return agg

    def get_mean_agg_level(self, od_matrix_agg):
        def weighted_res(h3_col, tree):
            levels = []
            for h in h3_col:
                node = tree.nodes.get(h)
                levels.append(node.resolution if node else tree.min_resolution)
            return levels

        od_matrix_agg['res_o'] = weighted_res(od_matrix_agg['start_gen'], self.lattice.tree_start)
        od_matrix_agg['res_d'] = weighted_res(od_matrix_agg['end_gen'], self.lattice.tree_end)

        od_matrix_agg['w_res_o'] = od_matrix_agg['res_o'] * od_matrix_agg['total_weight']
        od_matrix_agg['w_res_d'] = od_matrix_agg['res_d'] * od_matrix_agg['total_weight']

        mean_vals = od_matrix_agg[od_matrix_agg['total_weight'] >= self.lattice.k].agg({
            'w_res_o':'sum', 'w_res_d':'sum', 'total_weight':'sum'
        })

        if mean_vals['total_weight'] == 0:
            return np.inf

        return (mean_vals['w_res_o'] + mean_vals['w_res_d']) / mean_vals['total_weight']


def oigh(od_matrix, tree_start, tree_end, k, S):
    lat = Lattice2DWeight(od_matrix, tree_start, tree_end, k, S)
    lat.nodes[(lat.L_start, lat.L_end)].evaluate()
    return lat.od_matrix_agg

In [54]:
if mode == "SEX":
    od_matrix_generalized_man = oigh(od_matrix_man, tree_start_man, tree_end_man, k=10*media_peso, S=0)
    od_matrix_generalized_woman = oigh(od_matrix_woman, tree_start_woman, tree_end_woman, k=10*media_peso, S=0)

elif mode == "AGE":
    od_matrix_generalized_10_19 = oigh(od_matrix_10_19, tree_start_10_19, tree_end_10_19, k=10*media_peso, S=0)
    od_matrix_generalized_20_29 = oigh(od_matrix_20_29, tree_start_20_29, tree_end_20_29, k=10*media_peso, S=0)
    od_matrix_generalized_30_39 = oigh(od_matrix_30_39, tree_start_30_39, tree_end_30_39, k=10*media_peso, S=0)
    od_matrix_generalized_40_49 = oigh(od_matrix_40_49, tree_start_40_49, tree_end_40_49, k=10*media_peso, S=0)
    od_matrix_generalized_50_59 = oigh(od_matrix_50_59, tree_start_50_59, tree_end_50_59, k=10*media_peso, S=0)
    od_matrix_generalized_60_69 = oigh(od_matrix_60_69, tree_start_60_69, tree_end_60_69, k=10*media_peso, S=0)
    od_matrix_generalized_over70 = oigh(od_matrix_over70, tree_start_over70, tree_end_over70, k=10*media_peso, S=0)    

elif mode == "PRO_CAT":
    od_matrix_generalized_procat_1 = oigh(od_matrix_procat_1, tree_start_procat_1, tree_end_procat_1, k=10*media_peso, S=0)
    od_matrix_generalized_procat_2 = oigh(od_matrix_procat_2, tree_start_procat_2, tree_end_procat_2, k=10*media_peso, S=0)
    od_matrix_generalized_procat_3 = oigh(od_matrix_procat_3, tree_start_procat_3, tree_end_procat_3, k=10*media_peso, S=0)
    od_matrix_generalized_procat_4 = oigh(od_matrix_procat_4, tree_start_procat_4, tree_end_procat_4, k=10*media_peso, S=0)
    od_matrix_generalized_procat_5 = oigh(od_matrix_procat_5, tree_start_procat_5, tree_end_procat_5, k=10*media_peso, S=0)
    od_matrix_generalized_procat_6 = oigh(od_matrix_procat_6, tree_start_procat_6, tree_end_procat_6, k=10*media_peso, S=0)
    od_matrix_generalized_procat_7 = oigh(od_matrix_procat_7, tree_start_procat_7, tree_end_procat_7, k=10*media_peso, S=0)
    od_matrix_generalized_procat_8 = oigh(od_matrix_procat_8, tree_start_procat_8, tree_end_procat_8, k=10*media_peso, S=0)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [55]:
import folium
import h3
import pandas as pd

class GeneralizedH3Visualizer:
    def __init__(self, od_matrix, center_lat=48.8566, center_lon=2.3522):
        """
        Visualizza una OD matrix generalizzata H3 su Folium.

        Args:
            od_matrix: DataFrame con colonne ['start_gen', 'end_gen', 'total_weight']
            center_lat, center_lon: coordinate del centro della mappa
        """
        self.od_matrix = od_matrix
        self.center_lat = center_lat
        self.center_lon = center_lon
        
        # Totali per origine e destinazione
        self.origin_flows = od_matrix.groupby('start_gen')['total_weight'].sum().to_dict()
        self.dest_flows = od_matrix.groupby('end_gen')['total_weight'].sum().to_dict()
    
    def _h3_to_geojson(self, h3_id):
        """Converte un esagono H3 in GeoJSON"""
        boundary = h3.cell_to_boundary(h3_id)
        coords = [[[lon, lat] for lat, lon in boundary]]  # GeoJSON vuole lon, lat
        return {
            "type": "Feature",
            "geometry": {"type": "Polygon", "coordinates": coords},
            "properties": {"h3_id": h3_id, "resolution": h3.get_resolution(h3_id)}
        }
    
    def create_map(self, max_hexagons=100, alpha=0.6, zoom_start=10):
        """Crea la mappa Folium con esagoni di origine e destinazione"""
        m = folium.Map(location=[self.center_lat, self.center_lon], zoom_start=zoom_start, tiles='OpenStreetMap')
        
        # Layer Origini (blu)
        origins_sorted = sorted(self.origin_flows.items(), key=lambda x: x[1], reverse=True)[:max_hexagons]
        origin_layer = folium.FeatureGroup(name="Origini (blu)", show=True)
        if origins_sorted:
            min_flow, max_flow = min(v for _, v in origins_sorted), max(v for _, v in origins_sorted)
            for h3_id, weight in origins_sorted:
                geojson = self._h3_to_geojson(h3_id)
                intensity = (weight - min_flow) / (max_flow - min_flow) if max_flow > min_flow else 1.0
                blue_intensity = int(255 * (0.3 + 0.7*intensity))
                fill_color = f"#{0:02x}{0:02x}{blue_intensity:02x}"
                folium.GeoJson(
                    geojson,
                    style_function=lambda x, fill_color=fill_color: {
                        'fillColor': fill_color,
                        'color': 'darkblue',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    tooltip=f"{weight:.2f} peso totale"
                ).add_to(origin_layer)
        origin_layer.add_to(m)
        
        # Layer Destinazioni (rosso)
        dest_sorted = sorted(self.dest_flows.items(), key=lambda x: x[1], reverse=True)[:max_hexagons]
        dest_layer = folium.FeatureGroup(name="Destinazioni (rosso)", show=True)
        if dest_sorted:
            min_flow, max_flow = min(v for _, v in dest_sorted), max(v for _, v in dest_sorted)
            for h3_id, weight in dest_sorted:
                geojson = self._h3_to_geojson(h3_id)
                intensity = (weight - min_flow) / (max_flow - min_flow) if max_flow > min_flow else 1.0
                red_intensity = int(255 * (0.3 + 0.7*intensity))
                fill_color = f"#{red_intensity:02x}{0:02x}{0:02x}"
                folium.GeoJson(
                    geojson,
                    style_function=lambda x, fill_color=fill_color: {
                        'fillColor': fill_color,
                        'color': 'darkred',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    tooltip=f"{weight:.2f} peso totale"
                ).add_to(dest_layer)
        dest_layer.add_to(m)
        
        folium.LayerControl().add_to(m)
        return m

In [56]:
if mode == "SEX":
    visualizer_man = GeneralizedH3Visualizer(od_matrix_generalized_man)
    visualizer_woman = GeneralizedH3Visualizer(od_matrix_generalized_woman)

    mappa_man = visualizer_man.create_map(max_hexagons=2000000)
    mappa_woman = visualizer_woman.create_map(max_hexagons=2000000)

    display(mappa_man)
    display(mappa_woman)

elif mode == "AGE":
    visualizer_10_19 = GeneralizedH3Visualizer(od_matrix_generalized_10_19)
    visualizer_20_29 = GeneralizedH3Visualizer(od_matrix_generalized_20_29)
    visualizer_30_39 = GeneralizedH3Visualizer(od_matrix_generalized_30_39)
    visualizer_40_49 = GeneralizedH3Visualizer(od_matrix_generalized_40_49)
    visualizer_50_59 = GeneralizedH3Visualizer(od_matrix_generalized_50_59)
    visualizer_60_69 = GeneralizedH3Visualizer(od_matrix_generalized_60_69)
    visualizer_over70 = GeneralizedH3Visualizer(od_matrix_generalized_over70)

    mappa_10_19 = visualizer_10_19.create_map(max_hexagons=2000000)
    mappa_20_29 = visualizer_20_29.create_map(max_hexagons=2000000)
    mappa_30_39 = visualizer_30_39.create_map(max_hexagons=2000000)
    mappa_40_49 = visualizer_40_49.create_map(max_hexagons=2000000)
    mappa_50_59 = visualizer_50_59.create_map(max_hexagons=2000000)
    mappa_60_69 = visualizer_60_69.create_map(max_hexagons=2000000)
    mappa_over70 = visualizer_over70.create_map(max_hexagons=2000000)

    display(mappa_10_19)
    display(mappa_20_29)
    display(mappa_30_39)
    display(mappa_40_49)
    display(mappa_50_59)
    display(mappa_60_69)
    display(mappa_over70)

elif mode == "PRO_CAT":
    visualizer_procat_1 = GeneralizedH3Visualizer(od_matrix_generalized_procat_1)
    visualizer_procat_2 = GeneralizedH3Visualizer(od_matrix_generalized_procat_2)
    visualizer_procat_3 = GeneralizedH3Visualizer(od_matrix_generalized_procat_3)
    visualizer_procat_4 = GeneralizedH3Visualizer(od_matrix_generalized_procat_4)
    visualizer_procat_5 = GeneralizedH3Visualizer(od_matrix_generalized_procat_5)
    visualizer_procat_6 = GeneralizedH3Visualizer(od_matrix_generalized_procat_6)
    visualizer_procat_7 = GeneralizedH3Visualizer(od_matrix_generalized_procat_7)
    visualizer_procat_8 = GeneralizedH3Visualizer(od_matrix_generalized_procat_8)

    mappa_procat_1 = visualizer_procat_1.create_map(max_hexagons=2000000)
    mappa_procat_2 = visualizer_procat_2.create_map(max_hexagons=2000000)
    mappa_procat_3 = visualizer_procat_3.create_map(max_hexagons=2000000)
    mappa_procat_4 = visualizer_procat_4.create_map(max_hexagons=2000000)
    mappa_procat_5 = visualizer_procat_5.create_map(max_hexagons=2000000)
    mappa_procat_6 = visualizer_procat_6.create_map(max_hexagons=2000000)
    mappa_procat_7 = visualizer_procat_7.create_map(max_hexagons=2000000)
    mappa_procat_8 = visualizer_procat_8.create_map(max_hexagons=2000000)

    display(mappa_procat_1)
    display(mappa_procat_2)
    display(mappa_procat_3)
    display(mappa_procat_4)
    display(mappa_procat_5)
    display(mappa_procat_6)
    display(mappa_procat_7)
    display(mappa_procat_8)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [57]:
import numpy as np
import pandas as pd

def compute_discernability_and_cavg(df: pd.DataFrame, k: int, suppressed_count: int = 0) -> dict:
    """
    Calcola C_DM e C_AVG per un dataset OD generalizzato.
    
    Args:
        df: DataFrame con colonne ['start_h3', 'end_h3', 'count']
        k: soglia k-anonimity
        suppressed_count: numero di coppie OD soppressi (facoltativo)
    
    Returns:
        dict con C_DM, C_AVG, numero totale record e classi equivalenza
    """
    counts = df['count'].values
    total_records = counts.sum() + suppressed_count
    total_equiv_classes = len(counts) + suppressed_count
    
    # C_DM: somma dei quadrati dei count >= k
    k_anonymous_counts = counts[counts >= k]
    c_dm_gen = np.sum(k_anonymous_counts**2)
    
    # Penalità per record soppressi
    suppression_penalty = suppressed_count * counts.sum()  # o totale record, a seconda della definizione
    c_dm = c_dm_gen + suppression_penalty
    
    # C_AVG: (total_records / total_equiv_classes) / k
    c_avg = (total_records / total_equiv_classes) / k if total_equiv_classes > 0 else float('inf')
    
    return {
        'C_DM': c_dm,
        'C_AVG': c_avg,
        'total_records': total_records,
        'total_equivalence_classes': total_equiv_classes,
        'k': k
    }

if mode == "SEX":
    metrics_man = compute_discernability_and_cavg(od_matrix_generalized_man, k=10, suppressed_count=0)
    metrics_woman = compute_discernability_and_cavg(od_matrix_generalized_woman, k=10, suppressed_count=0)

    print("\n--- SEX ---")
    print(f"Man    → C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    print(f"Woman  → C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    metrics_10_19 = compute_discernability_and_cavg(od_matrix_generalized_10_19, k=10, suppressed_count=0)
    metrics_20_29 = compute_discernability_and_cavg(od_matrix_generalized_20_29, k=10, suppressed_count=0)
    metrics_30_39 = compute_discernability_and_cavg(od_matrix_generalized_30_39, k=10, suppressed_count=0)
    metrics_40_49 = compute_discernability_and_cavg(od_matrix_generalized_40_49, k=10, suppressed_count=0)
    metrics_50_59 = compute_discernability_and_cavg(od_matrix_generalized_50_59, k=10, suppressed_count=0)
    metrics_60_69 = compute_discernability_and_cavg(od_matrix_generalized_60_69, k=10, suppressed_count=0)
    metrics_over70 = compute_discernability_and_cavg(od_matrix_generalized_over70, k=10, suppressed_count=0)

    print("\n--- AGE ---")
    print(f"10-19  → C_DM: {metrics_10_19['C_DM']:,} | C_AVG: {metrics_10_19['C_AVG']:.4f}")
    print(f"20-29  → C_DM: {metrics_20_29['C_DM']:,} | C_AVG: {metrics_20_29['C_AVG']:.4f}")
    print(f"30-39  → C_DM: {metrics_30_39['C_DM']:,} | C_AVG: {metrics_30_39['C_AVG']:.4f}")
    print(f"40-49  → C_DM: {metrics_40_49['C_DM']:,} | C_AVG: {metrics_40_49['C_AVG']:.4f}")
    print(f"50-59  → C_DM: {metrics_50_59['C_DM']:,} | C_AVG: {metrics_50_59['C_AVG']:.4f}")
    print(f"60-69  → C_DM: {metrics_60_69['C_DM']:,} | C_AVG: {metrics_60_69['C_AVG']:.4f}")
    print(f"Over70 → C_DM: {metrics_over70['C_DM']:,} | C_AVG: {metrics_over70['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    metrics_procat_1 = compute_discernability_and_cavg(od_matrix_generalized_procat_1, k=10, suppressed_count=0)
    metrics_procat_2 = compute_discernability_and_cavg(od_matrix_generalized_procat_2, k=10, suppressed_count=0)
    metrics_procat_3 = compute_discernability_and_cavg(od_matrix_generalized_procat_3, k=10, suppressed_count=0)
    metrics_procat_4 = compute_discernability_and_cavg(od_matrix_generalized_procat_4, k=10, suppressed_count=0)
    metrics_procat_5 = compute_discernability_and_cavg(od_matrix_generalized_procat_5, k=10, suppressed_count=0)
    metrics_procat_6 = compute_discernability_and_cavg(od_matrix_generalized_procat_6, k=10, suppressed_count=0)
    metrics_procat_7 = compute_discernability_and_cavg(od_matrix_generalized_procat_7, k=10, suppressed_count=0)
    metrics_procat_8 = compute_discernability_and_cavg(od_matrix_generalized_procat_8, k=10, suppressed_count=0)

    print("\n--- PRO_CAT ---")
    print(f"Cat 1 → C_DM: {metrics_procat_1['C_DM']:,} | C_AVG: {metrics_procat_1['C_AVG']:.4f}")
    print(f"Cat 2 → C_DM: {metrics_procat_2['C_DM']:,} | C_AVG: {metrics_procat_2['C_AVG']:.4f}")
    print(f"Cat 3 → C_DM: {metrics_procat_3['C_DM']:,} | C_AVG: {metrics_procat_3['C_AVG']:.4f}")
    print(f"Cat 4 → C_DM: {metrics_procat_4['C_DM']:,} | C_AVG: {metrics_procat_4['C_AVG']:.4f}")
    print(f"Cat 5 → C_DM: {metrics_procat_5['C_DM']:,} | C_AVG: {metrics_procat_5['C_AVG']:.4f}")
    print(f"Cat 6 → C_DM: {metrics_procat_6['C_DM']:,} | C_AVG: {metrics_procat_6['C_AVG']:.4f}")
    print(f"Cat 7 → C_DM: {metrics_procat_7['C_DM']:,} | C_AVG: {metrics_procat_7['C_AVG']:.4f}")
    print(f"Cat 8 → C_DM: {metrics_procat_8['C_DM']:,} | C_AVG: {metrics_procat_8['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---
Cat 1 → C_DM: 348,571 | C_AVG: 21.7000
Cat 2 → C_DM: 4,310,302 | C_AVG: 27.5886
Cat 3 → C_DM: 871,026 | C_AVG: 12.0400
Cat 4 → C_DM: 3,120,245 | C_AVG: 72.5000
Cat 5 → C_DM: 169,302 | C_AVG: 16.8000
Cat 6 → C_DM: 2,452,863 | C_AVG: 60.3800
Cat 7 → C_DM: 4,337,132 | C_AVG: 84.4000
Cat 8 → C_DM: 545,310 | C_AVG: 30.8800


In [58]:
from geopy.distance import geodesic

def calculate_generalization_distance_metric(df: pd.DataFrame, od_matrix_generalized: pd.DataFrame) -> Dict:
   
   print("🔍 Calcolo metrica di distanza post-generalizzazione...")
   
   # 1. Crea mapping da esagoni originali a esagoni generalizzati
   start_original_to_generalized = {}
   end_original_to_generalized = {}
   
   # Ottieni tutti gli esagoni generalizzati unici
   generalized_start_h3 = set(od_matrix_generalized['start_gen'].unique())
   generalized_end_h3 = set(od_matrix_generalized['end_gen'].unique())
   
   # Per ogni esagono originale, trova l'esagono generalizzato corrispondente
   unique_start_h3 = df['start_h3'].unique()
   unique_end_h3 = df['end_h3'].unique()
   
   print(f"📊 Mappatura {len(unique_start_h3)} esagoni origine...")
   for original_h3 in unique_start_h3:
       generalized_h3 = find_generalized_hexagon(original_h3, generalized_start_h3)
       if generalized_h3:
           start_original_to_generalized[original_h3] = generalized_h3
   
   print(f"📊 Mappatura {len(unique_end_h3)} esagoni destinazione...")
   for original_h3 in unique_end_h3:
       generalized_h3 = find_generalized_hexagon(original_h3, generalized_end_h3)
       if generalized_h3:
           end_original_to_generalized[original_h3] = generalized_h3
   
   # 3. Calcola distanze per i punti di partenza
   start_distances = []
   start_coords = []
   
   for idx, row in df.iterrows():
       original_h3 = row['start_h3']
       original_coords = (row['start_lat'], row['start_lon'])
       
       if original_h3 in start_original_to_generalized:
           generalized_h3 = start_original_to_generalized[original_h3]
           generalized_coords = h3.cell_to_latlng(generalized_h3)
           
           distance = geodesic(original_coords, generalized_coords).meters
           
           start_distances.append(distance)
           start_coords.append({
               'original_h3': original_h3,
               'generalized_h3': generalized_h3,
               'original_coords': original_coords,
               'generalized_coords': generalized_coords,
               'distance': distance
           })
   
   # 4. Calcola distanze per i punti di destinazione
   end_distances = []
   end_coords = []
   
   for idx, row in df.iterrows():
       original_h3 = row['end_h3']
       original_coords = (row['end_lat'], row['end_lon'])
       
       if original_h3 in end_original_to_generalized:
           generalized_h3 = end_original_to_generalized[original_h3]
           generalized_coords = h3.cell_to_latlng(generalized_h3)
           
           distance = geodesic(original_coords, generalized_coords).meters
               
           end_distances.append(distance)
           end_coords.append({
               'original_h3': original_h3,
               'generalized_h3': generalized_h3,
               'original_coords': original_coords,
               'generalized_coords': generalized_coords,
               'distance': distance
           })
   
   # 5. Calcola statistiche
   results = {
       'start_distances': {
           'mean': np.mean(start_distances) if start_distances else 0,
           'median': np.median(start_distances) if start_distances else 0,
           'std': np.std(start_distances) if start_distances else 0,
           'min': np.min(start_distances) if start_distances else 0,
           'max': np.max(start_distances) if start_distances else 0,
           'count': len(start_distances)
       },
       'end_distances': {
           'mean': np.mean(end_distances) if end_distances else 0,
           'median': np.median(end_distances) if end_distances else 0,
           'std': np.std(end_distances) if end_distances else 0,
           'min': np.min(end_distances) if end_distances else 0,
           'max': np.max(end_distances) if end_distances else 0,
           'count': len(end_distances)
       },
       'overall': {
           'mean': np.mean(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'median': np.median(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'std': np.std(start_distances + end_distances) if (start_distances or end_distances) else 0,
           'total_points': len(start_distances) + len(end_distances)
       },
       'mappings': {
           'start_original_to_generalized': start_original_to_generalized,
           'end_original_to_generalized': end_original_to_generalized
       },
       'detailed_coords': {
           'start': start_coords,
           'end': end_coords
       }
   }
   
   # 6. Stampa risultati
   print("\n" + "="*60)
   print("📏 METRICHE DI DISTANZA POST-GENERALIZZAZIONE")
   print("="*60)
   
   print(f"\n🎯 PUNTI DI PARTENZA:")
   print(f"   • Distanza media: {results['start_distances']['mean']:.2f} metri")
   print(f"   • Distanza mediana: {results['start_distances']['median']:.2f} metri")
   print(f"   • Deviazione standard: {results['start_distances']['std']:.2f} metri")
   print(f"   • Min-Max: {results['start_distances']['min']:.2f} - {results['start_distances']['max']:.2f} metri")
   print(f"   • Punti analizzati: {results['start_distances']['count']:,}")
   
   print(f"\n🏁 PUNTI DI DESTINAZIONE:")
   print(f"   • Distanza media: {results['end_distances']['mean']:.2f} metri")
   print(f"   • Distanza mediana: {results['end_distances']['median']:.2f} metri")
   print(f"   • Deviazione standard: {results['end_distances']['std']:.2f} metri")
   print(f"   • Min-Max: {results['end_distances']['min']:.2f} - {results['end_distances']['max']:.2f} metri")
   print(f"   • Punti analizzati: {results['end_distances']['count']:,}")
   
   print(f"\n🌍 COMPLESSIVO:")
   print(f"   • Distanza media totale: {results['overall']['mean']:.2f} metri")
   print(f"   • Distanza mediana totale: {results['overall']['median']:.2f} metri")
   print(f"   • Deviazione standard totale: {results['overall']['std']:.2f} metri")
   print(f"   • Punti totali: {results['overall']['total_points']:,}")
   
   return results

def find_generalized_hexagon(original_h3: str, generalized_hexagons: set) -> str:
   """
   Trova l'esagono generalizzato corrispondente a un esagono originale
   """
   # Se l'esagono è già nella lista degli esagoni generalizzati
   if original_h3 in generalized_hexagons:
       return original_h3
   
   # Altrimenti cerca tra tutti gli esagoni generalizzati se l'originale è loro discendente
   for generalized_h3 in generalized_hexagons:
       if is_descendant_of(original_h3, generalized_h3):
           return generalized_h3
   
   return None

def is_descendant_of(child_h3: str, parent_h3: str) -> bool:
   """
   Controlla se child_h3 è discendente di parent_h3
   """
   child_res = h3.get_resolution(child_h3)
   parent_res = h3.get_resolution(parent_h3)
   
   if parent_res >= child_res:
       return False
   
   current = child_h3
   while h3.get_resolution(current) > parent_res:
       current = h3.cell_to_parent(current, h3.get_resolution(current) - 1)
   
   return current == parent_h3

def analyze_generalization_impact(results: Dict) -> None:
   """
   Analizza l'impatto della generalizzazione sulle distanze
   """
   print("\n" + "="*60)
   print("📊 ANALISI IMPATTO GENERALIZZAZIONE")
   print("="*60)
   
   # Calcola percentili
   all_distances = []
   for coord in results['detailed_coords']['start'] + results['detailed_coords']['end']:
       all_distances.append(coord['distance'])
   
   if all_distances:
       percentiles = [25, 50, 75, 90, 95, 99]
       print("\n📏 Distribuzione distanze:")
       for p in percentiles:
           value = np.percentile(all_distances, p)
           print(f"   • {p}° percentile: {value:.2f} metri")
   
   # Analizza per risoluzione
   resolution_analysis = {}
   for coord in results['detailed_coords']['start'] + results['detailed_coords']['end']:
       original_res = h3.get_resolution(coord['original_h3'])
       generalized_res = h3.get_resolution(coord['generalized_h3'])
       
       key = f"{original_res}→{generalized_res}"
       if key not in resolution_analysis:
           resolution_analysis[key] = []
       resolution_analysis[key].append(coord['distance'])
   
   print("\n🔍 Analisi per risoluzione:")
   for resolution_change, distances in resolution_analysis.items():
       mean_dist = np.mean(distances)
       count = len(distances)
       print(f"   • {resolution_change}: {mean_dist:.2f}m (n={count})")

if mode == "SEX":
    print("\n--- SEX ---")

    print("\n[Man]")
    distance_results_man = calculate_generalization_distance_metric(
        df=filtered_df_man, 
        od_matrix_generalized=od_matrix_generalized_man
    )
    analyze_generalization_impact(distance_results_man)

    print("\n[Woman]")
    distance_results_woman = calculate_generalization_distance_metric(
        df=filtered_df_woman, 
        od_matrix_generalized=od_matrix_generalized_woman
    )
    analyze_generalization_impact(distance_results_woman)

elif mode == "AGE":
    print("\n--- AGE ---")

    print("\n[10-19]")
    distance_results_10_19 = calculate_generalization_distance_metric(
        df=filtered_df_10_19, 
        od_matrix_generalized=od_matrix_generalized_10_19
    )
    analyze_generalization_impact(distance_results_10_19)

    print("\n[20-29]")
    distance_results_20_29 = calculate_generalization_distance_metric(
        df=filtered_df_20_29, 
        od_matrix_generalized=od_matrix_generalized_20_29
    )
    analyze_generalization_impact(distance_results_20_29)

    print("\n[30-39]")
    distance_results_30_39 = calculate_generalization_distance_metric(
        df=filtered_df_30_39, 
        od_matrix_generalized=od_matrix_generalized_30_39
    )
    analyze_generalization_impact(distance_results_30_39)

    print("\n[40-49]")
    distance_results_40_49 = calculate_generalization_distance_metric(
        df=filtered_df_40_49, 
        od_matrix_generalized=od_matrix_generalized_40_49
    )
    analyze_generalization_impact(distance_results_40_49)

    print("\n[50-59]")
    distance_results_50_59 = calculate_generalization_distance_metric(
        df=filtered_df_50_59, 
        od_matrix_generalized=od_matrix_generalized_50_59
    )
    analyze_generalization_impact(distance_results_50_59)

    print("\n[60-69]")
    distance_results_60_69 = calculate_generalization_distance_metric(
        df=filtered_df_60_69, 
        od_matrix_generalized=od_matrix_generalized_60_69
    )
    analyze_generalization_impact(distance_results_60_69)

    print("\n[70+]")
    distance_results_over70 = calculate_generalization_distance_metric(
        df=filtered_df_over70, 
        od_matrix_generalized=od_matrix_generalized_over70
    )
    analyze_generalization_impact(distance_results_over70)

elif mode == "PRO_CAT":
    print("\n--- PRO_CAT ---")
    for i in range(1, 9):
        print(f"\n[Category {i}]")
        distance_results = calculate_generalization_distance_metric(
            df=globals()[f"filtered_df_procat_{i}"],
            od_matrix_generalized=globals()[f"od_matrix_generalized_procat_{i}"]
        )
        analyze_generalization_impact(distance_results)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---

[Category 1]
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 694 esagoni origine...
📊 Mappatura 734 esagoni destinazione...

📏 METRICHE DI DISTANZA POST-GENERALIZZAZIONE

🎯 PUNTI DI PARTENZA:
   • Distanza media: 14455.78 metri
   • Distanza mediana: 14128.09 metri
   • Deviazione standard: 2458.45 metri
   • Min-Max: 7231.30 - 23178.50 metri
   • Punti analizzati: 1,725

🏁 PUNTI DI DESTINAZIONE:
   • Distanza media: 2300.05 metri
   • Distanza mediana: 2476.82 metri
   • Deviazione standard: 841.14 metri
   • Min-Max: 68.67 - 3678.71 metri
   • Punti analizzati: 1,725

🌍 COMPLESSIVO:
   • Distanza media totale: 8377.91 metri
   • Distanza mediana totale: 5455.01 metri
   • Deviazione standard totale: 6349.50 metri
   • Punti totali: 3,450

📊 ANALISI IMPATTO GENERALIZZAZIONE

📏 Distribuzione distanze:
   • 25° percentile: 2476.92 metri
   • 50° percentile: 5455.01 metri
   • 75° percentile: 14128.02 metri
   • 90° percentile: 15886.12 metri
   • 95°

In [59]:
import pandas as pd
import h3

class GeneralizationMetric:
    """
    Ḡ = (1/V+) × Σ(|o| + |d|) × v_{o→d}
    """
    def __init__(self, k_threshold: int = 10):
        self.k_threshold = k_threshold

    def calculate_generalization_error(self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame) -> float:
        # Costruisci dizionari: generalizzato -> numero di celle originali
        origin_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="start_gen", column_orig="start_h3"
        )
        destination_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="end_gen", column_orig="end_h3"
        )

        total_volume_anonymous = 0
        weighted_count_sum = 0

        for _, row in od_matrix_generalized.iterrows():
            flow_value = row["count"]
            if flow_value >= self.k_threshold:
                origin_h3 = row["start_gen"]
                dest_h3   = row["end_gen"]

                origin_count = origin_counts.get(origin_h3, 1)
                dest_count   = destination_counts.get(dest_h3, 1)

                total_volume_anonymous += flow_value
                weighted_count_sum += (origin_count + dest_count) * flow_value

        return weighted_count_sum / total_volume_anonymous if total_volume_anonymous > 0 else 0.0

    def _build_hexagon_counts(
        self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame, 
        column_gen: str, column_orig: str
    ) -> dict:
        """
        Conta quanti esagoni originali appartengono a ciascun esagono generalizzato
        """
        generalized_hexagons = od_matrix_generalized[column_gen].unique()
        original_hexagons = od_matrix[column_orig].unique()

        counts = {}
        for gen_hex in generalized_hexagons:
            target_res = h3.get_resolution(gen_hex)

            # Trova tutti i parent degli originali alla risoluzione target
            parent_series = [h3.cell_to_parent(h, target_res) for h in original_hexagons]

            # Conta quante volte compare il parent == gen_hex
            count = sum(1 for p in parent_series if p == gen_hex)
            counts[gen_hex] = max(count, 1)  # fallback a 1

        return counts

metric = GeneralizationMetric(k_threshold=10)

if mode == "SEX":
    print("\n--- SEX ---")

    print("\n[Man]")
    error_man = metric.calculate_generalization_error(od_matrix_generalized_man, od_matrix_man)
    print(f"Errore di generalizzazione medio Ḡ (Man): {error_man:.3f}")

    print("\n[Woman]")
    error_woman = metric.calculate_generalization_error(od_matrix_generalized_woman, od_matrix_woman)
    print(f"Errore di generalizzazione medio Ḡ (Woman): {error_woman:.3f}")

elif mode == "AGE":
    print("\n--- AGE ---")

    print("\n[10-19]")
    error_10_19 = metric.calculate_generalization_error(od_matrix_generalized_10_19, od_matrix_10_19)
    print(f"Errore di generalizzazione medio Ḡ (10-19): {error_10_19:.3f}")

    print("\n[20-29]")
    error_20_29 = metric.calculate_generalization_error(od_matrix_generalized_20_29, od_matrix_20_29)
    print(f"Errore di generalizzazione medio Ḡ (20-29): {error_20_29:.3f}")

    print("\n[30-39]")
    error_30_39 = metric.calculate_generalization_error(od_matrix_generalized_30_39, od_matrix_30_39)
    print(f"Errore di generalizzazione medio Ḡ (30-39): {error_30_39:.3f}")

    print("\n[40-49]")
    error_40_49 = metric.calculate_generalization_error(od_matrix_generalized_40_49, od_matrix_40_49)
    print(f"Errore di generalizzazione medio Ḡ (40-49): {error_40_49:.3f}")

    print("\n[50-59]")
    error_50_59 = metric.calculate_generalization_error(od_matrix_generalized_50_59, od_matrix_50_59)
    print(f"Errore di generalizzazione medio Ḡ (50-59): {error_50_59:.3f}")

    print("\n[60-69]")
    error_60_69 = metric.calculate_generalization_error(od_matrix_generalized_60_69, od_matrix_60_69)
    print(f"Errore di generalizzazione medio Ḡ (60-69): {error_60_69:.3f}")

    print("\n[70+]")
    error_over70 = metric.calculate_generalization_error(od_matrix_generalized_over70, od_matrix_over70)
    print(f"Errore di generalizzazione medio Ḡ (70+): {error_over70:.3f}")

elif mode == "PRO_CAT":
    print("\n--- PRO_CAT ---")
    for i in range(1, 9):
        print(f"\n[Category {i}]")
        error = metric.calculate_generalization_error(
            globals()[f"od_matrix_generalized_procat_{i}"],
            globals()[f"od_matrix_procat_{i}"]
        )
        print(f"Errore di generalizzazione medio Ḡ (Cat {i}): {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---

[Category 1]
Errore di generalizzazione medio Ḡ (Cat 1): 909.481

[Category 2]
Errore di generalizzazione medio Ḡ (Cat 2): 4087.006

[Category 3]
Errore di generalizzazione medio Ḡ (Cat 3): 2222.519

[Category 4]
Errore di generalizzazione medio Ḡ (Cat 4): 2234.439

[Category 5]
Errore di generalizzazione medio Ḡ (Cat 5): 712.575

[Category 6]
Errore di generalizzazione medio Ḡ (Cat 6): 2132.098

[Category 7]
Errore di generalizzazione medio Ḡ (Cat 7): 2566.614

[Category 8]
Errore di generalizzazione medio Ḡ (Cat 8): 1215.010


In [60]:
def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                       od_matrix_generalized: pd.DataFrame) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    Versione ottimizzata, evita itertools.product su tutte le foglie.
    """
    # Dizionario dei flussi originali
    original_flows = {(row['start_h3'], row['end_h3']): row['count']
                      for _, row in original_od_df.iterrows()}

    total_volume = sum(original_flows.values())
    if total_volume == 0:
        return 0.0

    # Dizionario dei flussi generalizzati
    generalized_flows = {(row['start_gen'], row['end_gen']): row['count']
                         for _, row in od_matrix_generalized.iterrows()}

    gen_start_hexes = od_matrix_generalized['start_gen'].unique()
    gen_end_hexes   = od_matrix_generalized['end_gen'].unique()

    # Cache: gen_hex → leaves
    leaf_cache = {}

    def get_leaves(gen_hex, target_res):
        key = (gen_hex, target_res)
        if key in leaf_cache:
            return leaf_cache[key]
        res = h3.get_resolution(gen_hex)
        leaves = {gen_hex} if res == target_res else set(h3.cell_to_children(gen_hex, target_res))
        leaf_cache[key] = leaves
        return leaves

    # Risoluzione target
    target_res_start = h3.get_resolution(original_od_df['start_h3'].iloc[0])
    target_res_end   = h3.get_resolution(original_od_df['end_h3'].iloc[0])

    # Precompute mappe: leaf → parent generalized
    start_leaf_to_parent = {}
    for gen in gen_start_hexes:
        for leaf in get_leaves(gen, target_res_start):
            start_leaf_to_parent[leaf] = gen

    end_leaf_to_parent = {}
    for gen in gen_end_hexes:
        for leaf in get_leaves(gen, target_res_end):
            end_leaf_to_parent[leaf] = gen

    total_abs_error = 0.0

    # Itera solo sulle coppie presenti nell'originale
    for (s, d), true_count in original_flows.items():
        gen_s = start_leaf_to_parent.get(s)
        gen_d = end_leaf_to_parent.get(d)

        if gen_s is None or gen_d is None:
            reconstructed_count = 0.0
        else:
            gen_count = generalized_flows.get((gen_s, gen_d), 0.0)
            start_leaves = get_leaves(gen_s, target_res_start)
            end_leaves   = get_leaves(gen_d, target_res_end)
            reconstructed_count = gen_count / (len(start_leaves) * len(end_leaves))

        total_abs_error += abs(reconstructed_count - true_count)

    # Aggiungi errore per le coppie con count=0 nei generalized flows
    for (gen_s, gen_d), gen_count in generalized_flows.items():
        start_leaves = get_leaves(gen_s, target_res_start)
        end_leaves   = get_leaves(gen_d, target_res_end)
        count_per_leaf = gen_count / (len(start_leaves) * len(end_leaves))

        # Sottrai le coppie già contate
        for s in start_leaves:
            for d in end_leaves:
                if (s, d) not in original_flows:
                    total_abs_error += abs(count_per_leaf - 0.0)

    return total_abs_error / total_volume


def _find_generalized_parent(original_h3: str, generalized_hexagons: list) -> str:
    """
    Trova l'esagono generalizzato che contiene l'esagono originale.
    """
    original_res = h3.get_resolution(original_h3)
    
    for gen_hex in generalized_hexagons:
        gen_res = h3.get_resolution(gen_hex)
        if gen_res <= original_res:
            parent = h3.cell_to_parent(original_h3, gen_res)
            if parent == gen_hex:
                return gen_hex
    return None

if mode == "SEX":
    print("\n--- SEX ---")

    print("\n[Man]")
    loss_man = fast_reconstruction_loss(
        original_od_df=od_matrix_man,
        od_matrix_generalized=od_matrix_generalized_man
    )
    print(f"Reconstruction Loss (Man): {loss_man:.6f}")

    print("\n[Woman]")
    loss_woman = fast_reconstruction_loss(
        original_od_df=od_matrix_woman,
        od_matrix_generalized=od_matrix_generalized_woman
    )
    print(f"Reconstruction Loss (Woman): {loss_woman:.6f}")

elif mode == "AGE":
    print("\n--- AGE ---")

    print("\n[10-19]")
    loss_10_19 = fast_reconstruction_loss(
        original_od_df=od_matrix_10_19,
        od_matrix_generalized=od_matrix_generalized_10_19
    )
    print(f"Reconstruction Loss (10-19): {loss_10_19:.6f}")

    print("\n[20-29]")
    loss_20_29 = fast_reconstruction_loss(
        original_od_df=od_matrix_20_29,
        od_matrix_generalized=od_matrix_generalized_20_29
    )
    print(f"Reconstruction Loss (20-29): {loss_20_29:.6f}")

    print("\n[30-39]")
    loss_30_39 = fast_reconstruction_loss(
        original_od_df=od_matrix_30_39,
        od_matrix_generalized=od_matrix_generalized_30_39
    )
    print(f"Reconstruction Loss (30-39): {loss_30_39:.6f}")

    print("\n[40-49]")
    loss_40_49 = fast_reconstruction_loss(
        original_od_df=od_matrix_40_49,
        od_matrix_generalized=od_matrix_generalized_40_49
    )
    print(f"Reconstruction Loss (40-49): {loss_40_49:.6f}")

    print("\n[50-59]")
    loss_50_59 = fast_reconstruction_loss(
        original_od_df=od_matrix_50_59,
        od_matrix_generalized=od_matrix_generalized_50_59
    )
    print(f"Reconstruction Loss (50-59): {loss_50_59:.6f}")

    print("\n[60-69]")
    loss_60_69 = fast_reconstruction_loss(
        original_od_df=od_matrix_60_69,
        od_matrix_generalized=od_matrix_generalized_60_69
    )
    print(f"Reconstruction Loss (60-69): {loss_60_69:.6f}")

    print("\n[70+]")
    loss_over70 = fast_reconstruction_loss(
        original_od_df=od_matrix_over70,
        od_matrix_generalized=od_matrix_generalized_over70
    )
    print(f"Reconstruction Loss (70+): {loss_over70:.6f}")

elif mode == "PRO_CAT":
    print("\n--- PRO_CAT ---")
    for i in range(1, 9):
        print(f"\n[Category {i}]")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_procat_{i}"],
            od_matrix_generalized=globals()[f"od_matrix_generalized_procat_{i}"]
        )
        print(f"Reconstruction Loss (Cat {i}): {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- PRO_CAT ---

[Category 1]
Reconstruction Loss (Cat 1): 1.999998

[Category 2]
Reconstruction Loss (Cat 2): 1.999981

[Category 3]
Reconstruction Loss (Cat 3): 1.999991

[Category 4]
Reconstruction Loss (Cat 4): 1.999995

[Category 5]
Reconstruction Loss (Cat 5): 1.999999

[Category 6]
Reconstruction Loss (Cat 6): 1.999995

[Category 7]
Reconstruction Loss (Cat 7): 1.999994

[Category 8]
Reconstruction Loss (Cat 8): 1.999998


### Metriche con weight

In [61]:
import numpy as np
import pandas as pd

def compute_discernability_and_cavg(df: pd.DataFrame, k: int, suppressed_count: int = 0) -> dict:
    """
    Calcola C_DM e C_AVG per un dataset OD generalizzato.
    
    Args:
        df: DataFrame con colonne ['start_h3', 'end_h3', 'count']
        k: soglia k-anonimity
        suppressed_count: numero di coppie OD soppressi (facoltativo)
    
    Returns:
        dict con C_DM, C_AVG, numero totale record e classi equivalenza
    """
    counts = df['total_weight'].values
    total_records = counts.sum() + suppressed_count
    total_equiv_classes = len(counts) + suppressed_count
    
    # C_DM: somma dei quadrati dei count >= k
    k_anonymous_counts = counts[counts >= k]
    c_dm_gen = np.sum(k_anonymous_counts**2)
    
    # Penalità per record soppressi
    suppression_penalty = suppressed_count * counts.sum()  # o totale record, a seconda della definizione
    c_dm = c_dm_gen + suppression_penalty
    
    # C_AVG: (total_records / total_equiv_classes) / k
    c_avg = (total_records / total_equiv_classes) / k if total_equiv_classes > 0 else float('inf')
    
    return {
        'C_DM': c_dm,
        'C_AVG': c_avg,
        'total_records': total_records,
        'total_equivalence_classes': total_equiv_classes,
        'k': k
    }

if mode == "SEX":
    metrics_man = compute_discernability_and_cavg(od_matrix_generalized_man, k=10*media_peso, suppressed_count=0)
    metrics_woman = compute_discernability_and_cavg(od_matrix_generalized_woman, k=10*media_peso, suppressed_count=0)

    print("\n--- SEX ---")
    print(f"Man    → C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    print(f"Woman  → C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    metrics_10_19 = compute_discernability_and_cavg(od_matrix_generalized_10_19, k=10*media_peso, suppressed_count=0)
    metrics_20_29 = compute_discernability_and_cavg(od_matrix_generalized_20_29, k=10*media_peso, suppressed_count=0)
    metrics_30_39 = compute_discernability_and_cavg(od_matrix_generalized_30_39, k=10*media_peso, suppressed_count=0)
    metrics_40_49 = compute_discernability_and_cavg(od_matrix_generalized_40_49, k=10*media_peso, suppressed_count=0)
    metrics_50_59 = compute_discernability_and_cavg(od_matrix_generalized_50_59, k=10*media_peso, suppressed_count=0)
    metrics_60_69 = compute_discernability_and_cavg(od_matrix_generalized_60_69, k=10*media_peso, suppressed_count=0)
    metrics_over70 = compute_discernability_and_cavg(od_matrix_generalized_over70, k=10*media_peso, suppressed_count=0)

    print("\n--- AGE ---")
    print(f"10-19  → C_DM: {metrics_10_19['C_DM']:,} | C_AVG: {metrics_10_19['C_AVG']:.4f}")
    print(f"20-29  → C_DM: {metrics_20_29['C_DM']:,} | C_AVG: {metrics_20_29['C_AVG']:.4f}")
    print(f"30-39  → C_DM: {metrics_30_39['C_DM']:,} | C_AVG: {metrics_30_39['C_AVG']:.4f}")
    print(f"40-49  → C_DM: {metrics_40_49['C_DM']:,} | C_AVG: {metrics_40_49['C_AVG']:.4f}")
    print(f"50-59  → C_DM: {metrics_50_59['C_DM']:,} | C_AVG: {metrics_50_59['C_AVG']:.4f}")
    print(f"60-69  → C_DM: {metrics_60_69['C_DM']:,} | C_AVG: {metrics_60_69['C_AVG']:.4f}")
    print(f"Over70 → C_DM: {metrics_over70['C_DM']:,} | C_AVG: {metrics_over70['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    metrics_procat_1 = compute_discernability_and_cavg(od_matrix_generalized_procat_1, k=10*media_peso, suppressed_count=0)
    metrics_procat_2 = compute_discernability_and_cavg(od_matrix_generalized_procat_2, k=10*media_peso, suppressed_count=0)
    metrics_procat_3 = compute_discernability_and_cavg(od_matrix_generalized_procat_3, k=10*media_peso, suppressed_count=0)
    metrics_procat_4 = compute_discernability_and_cavg(od_matrix_generalized_procat_4, k=10*media_peso, suppressed_count=0)
    metrics_procat_5 = compute_discernability_and_cavg(od_matrix_generalized_procat_5, k=10*media_peso, suppressed_count=0)
    metrics_procat_6 = compute_discernability_and_cavg(od_matrix_generalized_procat_6, k=10*media_peso, suppressed_count=0)
    metrics_procat_7 = compute_discernability_and_cavg(od_matrix_generalized_procat_7, k=10*media_peso, suppressed_count=0)
    metrics_procat_8 = compute_discernability_and_cavg(od_matrix_generalized_procat_8, k=10*media_peso, suppressed_count=0)

    print("\n--- PRO_CAT ---")
    print(f"Cat 1 → C_DM: {metrics_procat_1['C_DM']:,} | C_AVG: {metrics_procat_1['C_AVG']:.4f}")
    print(f"Cat 2 → C_DM: {metrics_procat_2['C_DM']:,} | C_AVG: {metrics_procat_2['C_AVG']:.4f}")
    print(f"Cat 3 → C_DM: {metrics_procat_3['C_DM']:,} | C_AVG: {metrics_procat_3['C_AVG']:.4f}")
    print(f"Cat 4 → C_DM: {metrics_procat_4['C_DM']:,} | C_AVG: {metrics_procat_4['C_AVG']:.4f}")
    print(f"Cat 5 → C_DM: {metrics_procat_5['C_DM']:,} | C_AVG: {metrics_procat_5['C_AVG']:.4f}")
    print(f"Cat 6 → C_DM: {metrics_procat_6['C_DM']:,} | C_AVG: {metrics_procat_6['C_AVG']:.4f}")
    print(f"Cat 7 → C_DM: {metrics_procat_7['C_DM']:,} | C_AVG: {metrics_procat_7['C_AVG']:.4f}")
    print(f"Cat 8 → C_DM: {metrics_procat_8['C_DM']:,} | C_AVG: {metrics_procat_8['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---
Cat 1 → C_DM: 1,537,637,844,556.5728 | C_AVG: 17.7418
Cat 2 → C_DM: 15,739,852,693,966.727 | C_AVG: 19.3226
Cat 3 → C_DM: 8,055,318,247,859.692 | C_AVG: 13.7182
Cat 4 → C_DM: 47,322,270,922,161.69 | C_AVG: 104.1199
Cat 5 → C_DM: 2,435,852,454,649.1216 | C_AVG: 23.1393
Cat 6 → C_DM: 23,722,344,974,356.277 | C_AVG: 70.2374
Cat 7 → C_DM: 22,833,812,872,485.297 | C_AVG: 73.1057
Cat 8 → C_DM: 2,742,991,389,322.0415 | C_AVG: 23.7153


In [62]:
import pandas as pd
import h3

class GeneralizationMetric:
    """
    Ḡ = (1/V+) × Σ(|o| + |d|) × v_{o→d}
    """
    def __init__(self, k_threshold: int = 10):
        self.k_threshold = k_threshold

    def calculate_generalization_error(self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame) -> float:
        # Costruisci dizionari: generalizzato -> numero di celle originali
        origin_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="start_gen", column_orig="start_h3"
        )
        destination_counts = self._build_hexagon_counts(
            od_matrix_generalized, od_matrix, column_gen="end_gen", column_orig="end_h3"
        )

        total_volume_anonymous = 0
        weighted_count_sum = 0

        for _, row in od_matrix_generalized.iterrows():
            flow_value = row["total_weight"]
            if flow_value >= self.k_threshold:
                origin_h3 = row["start_gen"]
                dest_h3   = row["end_gen"]

                origin_count = origin_counts.get(origin_h3, 1)
                dest_count   = destination_counts.get(dest_h3, 1)

                total_volume_anonymous += flow_value
                weighted_count_sum += (origin_count + dest_count) * flow_value

        return weighted_count_sum / total_volume_anonymous if total_volume_anonymous > 0 else 0.0

    def _build_hexagon_counts(
        self, od_matrix_generalized: pd.DataFrame, od_matrix: pd.DataFrame, 
        column_gen: str, column_orig: str
    ) -> dict:
        """
        Conta quanti esagoni originali appartengono a ciascun esagono generalizzato
        """
        generalized_hexagons = od_matrix_generalized[column_gen].unique()
        original_hexagons = od_matrix[column_orig].unique()

        counts = {}
        for gen_hex in generalized_hexagons:
            target_res = h3.get_resolution(gen_hex)

            # Trova tutti i parent degli originali alla risoluzione target
            parent_series = [h3.cell_to_parent(h, target_res) for h in original_hexagons]

            # Conta quante volte compare il parent == gen_hex
            count = sum(1 for p in parent_series if p == gen_hex)
            counts[gen_hex] = max(count, 1)  # fallback a 1

        return counts

metric = GeneralizationMetric(k_threshold=10*media_peso)

if mode == "SEX":
    print("\n--- SEX ---")

    print("\n[Man]")
    error_man = metric.calculate_generalization_error(od_matrix_generalized_man, od_matrix_man)
    print(f"Errore di generalizzazione medio Ḡ (Man): {error_man:.3f}")

    print("\n[Woman]")
    error_woman = metric.calculate_generalization_error(od_matrix_generalized_woman, od_matrix_woman)
    print(f"Errore di generalizzazione medio Ḡ (Woman): {error_woman:.3f}")

elif mode == "AGE":
    print("\n--- AGE ---")

    print("\n[10-19]")
    error_10_19 = metric.calculate_generalization_error(od_matrix_generalized_10_19, od_matrix_10_19)
    print(f"Errore di generalizzazione medio Ḡ (10-19): {error_10_19:.3f}")

    print("\n[20-29]")
    error_20_29 = metric.calculate_generalization_error(od_matrix_generalized_20_29, od_matrix_20_29)
    print(f"Errore di generalizzazione medio Ḡ (20-29): {error_20_29:.3f}")

    print("\n[30-39]")
    error_30_39 = metric.calculate_generalization_error(od_matrix_generalized_30_39, od_matrix_30_39)
    print(f"Errore di generalizzazione medio Ḡ (30-39): {error_30_39:.3f}")

    print("\n[40-49]")
    error_40_49 = metric.calculate_generalization_error(od_matrix_generalized_40_49, od_matrix_40_49)
    print(f"Errore di generalizzazione medio Ḡ (40-49): {error_40_49:.3f}")

    print("\n[50-59]")
    error_50_59 = metric.calculate_generalization_error(od_matrix_generalized_50_59, od_matrix_50_59)
    print(f"Errore di generalizzazione medio Ḡ (50-59): {error_50_59:.3f}")

    print("\n[60-69]")
    error_60_69 = metric.calculate_generalization_error(od_matrix_generalized_60_69, od_matrix_60_69)
    print(f"Errore di generalizzazione medio Ḡ (60-69): {error_60_69:.3f}")

    print("\n[70+]")
    error_over70 = metric.calculate_generalization_error(od_matrix_generalized_over70, od_matrix_over70)
    print(f"Errore di generalizzazione medio Ḡ (70+): {error_over70:.3f}")

elif mode == "PRO_CAT":
    print("\n--- PRO_CAT ---")
    for i in range(1, 9):
        print(f"\n[Category {i}]")
        error = metric.calculate_generalization_error(
            globals()[f"od_matrix_generalized_procat_{i}"],
            globals()[f"od_matrix_procat_{i}"]
        )
        print(f"Errore di generalizzazione medio Ḡ (Cat {i}): {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---

[Category 1]
Errore di generalizzazione medio Ḡ (Cat 1): 898.492

[Category 2]
Errore di generalizzazione medio Ḡ (Cat 2): 4089.879

[Category 3]
Errore di generalizzazione medio Ḡ (Cat 3): 2220.007

[Category 4]
Errore di generalizzazione medio Ḡ (Cat 4): 2230.335

[Category 5]
Errore di generalizzazione medio Ḡ (Cat 5): 715.639

[Category 6]
Errore di generalizzazione medio Ḡ (Cat 6): 2121.430

[Category 7]
Errore di generalizzazione medio Ḡ (Cat 7): 2561.250

[Category 8]
Errore di generalizzazione medio Ḡ (Cat 8): 1223.931


In [63]:
def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                       od_matrix_generalized: pd.DataFrame) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    Versione ottimizzata, evita itertools.product su tutte le foglie.
    """
    # Dizionario dei flussi originali
    original_flows = {(row['start_h3'], row['end_h3']): row['total_weight']
                      for _, row in original_od_df.iterrows()}

    total_volume = sum(original_flows.values())
    if total_volume == 0:
        return 0.0

    # Dizionario dei flussi generalizzati
    generalized_flows = {(row['start_gen'], row['end_gen']): row['total_weight']
                         for _, row in od_matrix_generalized.iterrows()}

    gen_start_hexes = od_matrix_generalized['start_gen'].unique()
    gen_end_hexes   = od_matrix_generalized['end_gen'].unique()

    # Cache: gen_hex → leaves
    leaf_cache = {}

    def get_leaves(gen_hex, target_res):
        key = (gen_hex, target_res)
        if key in leaf_cache:
            return leaf_cache[key]
        res = h3.get_resolution(gen_hex)
        leaves = {gen_hex} if res == target_res else set(h3.cell_to_children(gen_hex, target_res))
        leaf_cache[key] = leaves
        return leaves

    # Risoluzione target
    target_res_start = h3.get_resolution(original_od_df['start_h3'].iloc[0])
    target_res_end   = h3.get_resolution(original_od_df['end_h3'].iloc[0])

    # Precompute mappe: leaf → parent generalized
    start_leaf_to_parent = {}
    for gen in gen_start_hexes:
        for leaf in get_leaves(gen, target_res_start):
            start_leaf_to_parent[leaf] = gen

    end_leaf_to_parent = {}
    for gen in gen_end_hexes:
        for leaf in get_leaves(gen, target_res_end):
            end_leaf_to_parent[leaf] = gen

    total_abs_error = 0.0

    # Itera solo sulle coppie presenti nell'originale
    for (s, d), true_count in original_flows.items():
        gen_s = start_leaf_to_parent.get(s)
        gen_d = end_leaf_to_parent.get(d)

        if gen_s is None or gen_d is None:
            reconstructed_count = 0.0
        else:
            gen_count = generalized_flows.get((gen_s, gen_d), 0.0)
            start_leaves = get_leaves(gen_s, target_res_start)
            end_leaves   = get_leaves(gen_d, target_res_end)
            reconstructed_count = gen_count / (len(start_leaves) * len(end_leaves))

        total_abs_error += abs(reconstructed_count - true_count)

    # Aggiungi errore per le coppie con count=0 nei generalized flows
    for (gen_s, gen_d), gen_count in generalized_flows.items():
        start_leaves = get_leaves(gen_s, target_res_start)
        end_leaves   = get_leaves(gen_d, target_res_end)
        count_per_leaf = gen_count / (len(start_leaves) * len(end_leaves))

        # Sottrai le coppie già contate
        for s in start_leaves:
            for d in end_leaves:
                if (s, d) not in original_flows:
                    total_abs_error += abs(count_per_leaf - 0.0)

    return total_abs_error / total_volume


def _find_generalized_parent(original_h3: str, generalized_hexagons: list) -> str:
    """
    Trova l'esagono generalizzato che contiene l'esagono originale.
    """
    original_res = h3.get_resolution(original_h3)
    
    for gen_hex in generalized_hexagons:
        gen_res = h3.get_resolution(gen_hex)
        if gen_res <= original_res:
            parent = h3.cell_to_parent(original_h3, gen_res)
            if parent == gen_hex:
                return gen_hex
    return None

if mode == "SEX":
    print("\n--- SEX ---")

    print("\n[Man]")
    loss_man = fast_reconstruction_loss(
        original_od_df=od_matrix_man,
        od_matrix_generalized=od_matrix_generalized_man
    )
    print(f"Reconstruction Loss (Man): {loss_man:.6f}")

    print("\n[Woman]")
    loss_woman = fast_reconstruction_loss(
        original_od_df=od_matrix_woman,
        od_matrix_generalized=od_matrix_generalized_woman
    )
    print(f"Reconstruction Loss (Woman): {loss_woman:.6f}")

elif mode == "AGE":
    print("\n--- AGE ---")

    print("\n[10-19]")
    loss_10_19 = fast_reconstruction_loss(
        original_od_df=od_matrix_10_19,
        od_matrix_generalized=od_matrix_generalized_10_19
    )
    print(f"Reconstruction Loss (10-19): {loss_10_19:.6f}")

    print("\n[20-29]")
    loss_20_29 = fast_reconstruction_loss(
        original_od_df=od_matrix_20_29,
        od_matrix_generalized=od_matrix_generalized_20_29
    )
    print(f"Reconstruction Loss (20-29): {loss_20_29:.6f}")

    print("\n[30-39]")
    loss_30_39 = fast_reconstruction_loss(
        original_od_df=od_matrix_30_39,
        od_matrix_generalized=od_matrix_generalized_30_39
    )
    print(f"Reconstruction Loss (30-39): {loss_30_39:.6f}")

    print("\n[40-49]")
    loss_40_49 = fast_reconstruction_loss(
        original_od_df=od_matrix_40_49,
        od_matrix_generalized=od_matrix_generalized_40_49
    )
    print(f"Reconstruction Loss (40-49): {loss_40_49:.6f}")

    print("\n[50-59]")
    loss_50_59 = fast_reconstruction_loss(
        original_od_df=od_matrix_50_59,
        od_matrix_generalized=od_matrix_generalized_50_59
    )
    print(f"Reconstruction Loss (50-59): {loss_50_59:.6f}")

    print("\n[60-69]")
    loss_60_69 = fast_reconstruction_loss(
        original_od_df=od_matrix_60_69,
        od_matrix_generalized=od_matrix_generalized_60_69
    )
    print(f"Reconstruction Loss (60-69): {loss_60_69:.6f}")

    print("\n[70+]")
    loss_over70 = fast_reconstruction_loss(
        original_od_df=od_matrix_over70,
        od_matrix_generalized=od_matrix_generalized_over70
    )
    print(f"Reconstruction Loss (70+): {loss_over70:.6f}")

elif mode == "PRO_CAT":
    print("\n--- PRO_CAT ---")
    for i in range(1, 9):
        print(f"\n[Category {i}]")
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_procat_{i}"],
            od_matrix_generalized=globals()[f"od_matrix_generalized_procat_{i}"]
        )
        print(f"Reconstruction Loss (Cat {i}): {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



--- PRO_CAT ---

[Category 1]
Reconstruction Loss (Cat 1): 1.999998

[Category 2]
Reconstruction Loss (Cat 2): 1.999980

[Category 3]
Reconstruction Loss (Cat 3): 1.999991

[Category 4]
Reconstruction Loss (Cat 4): 1.999995

[Category 5]
Reconstruction Loss (Cat 5): 1.999999

[Category 6]
Reconstruction Loss (Cat 6): 1.999995

[Category 7]
Reconstruction Loss (Cat 7): 1.999994

[Category 8]
Reconstruction Loss (Cat 8): 1.999998
